# Comparison of the assay and hyperspectral datas

The assay file contains the `Hole_ID` of every drill core, their position in the drill, the chemical composition of the sample (Fe, Fe2O3, P, S, SiO2, Al2O3, MnO, Mn, CaO, K2O, MgO, Na2O, TiO2) and the loss-on-ignition percentage.
The hyperspectral file contains the `Hole_ID` of every borehole, their position in the drill, the chemical composition of each sample (Fe, Al2O3, SiO2, K2O, CaO, MgO, TiO2, P, S, Mn), the loss-on-ignition percentage and other informations about the minerals in the sample.

The common data between these two files are the `Hole_ID`, the depth, most columns about chemical composition (Fe, Al2O3, SiO2, K2O, CaO, MgO, TiO2, P, S, Mn) and the loss-on-ignition percentage.

In [ ]:
import numpy as np
import pandas as pd
import geolime as geo
from pyproj import CRS
import seaborn as sns
import pyvista as pv

pv.set_jupyter_backend('panel')


geo.Logger().set_level(25)
# Format Pandas display for clarity and readability
pd.set_option("display.max_rows", 10)
pd.set_option("display.max_columns", 500)

We want to compare the `Hole_ID` of the assay and hyperspectral file to know if they have some drill core in common.

First we need to import these data from `.csv` files.

## Merging Interval Files 

### Assay File reading and formatting

In [ ]:
assay = geo.datasets.load("rocklea_dome/assay.csv")
assay

Some columns have string values named LNR, replacing them to NaN will allow comparisons with other number columns

In [ ]:
assay.dtypes

In [ ]:
assay.eq("LNR").any()

In [ ]:
assay.replace("LNR", np.nan, inplace=True)
assay[["P", "S", "TiO2", "LOI"]] = assay[["P", "S", "TiO2", "LOI"]].apply(pd.to_numeric)

### Hyperspec File reading

In [ ]:
hyperspec = pd.read_csv("../data/hyperspec.csv")
hyperspec

### Merge Preparation

The comparison of the two datasets require to have the list of the different `Hole_ID` of both files. These lists also need to be turned into sets in order to compare them.

In [ ]:
colonne_assay = set(assay["Hole_ID"])
colonne_hyperspec = set(hyperspec["Hole_ID"])

Now we have two sets with the different drill core that have been analyzed for each method. 

In [ ]:
len(colonne_assay)

In [ ]:
len(colonne_hyperspec)

Next command will search all the `Hole_ID` both in the assay and hyperspec file.

In [ ]:
intersection = colonne_assay.intersection(colonne_hyperspec)

In [ ]:
len(intersection)

The intersection of these two files has the same length as the smallest set, so every `Hole_ID` of the hyperspectral file are in the assay.

The drill cores of the hyperspectral file are included in the assay file. Now we want to see if the common columns between these two files have the same values. First we need to filter the DataFrame of the assay file in order to keep only the `Hole_ID` that are in common with the hyperspectral file.

In [ ]:
intersection = list(intersection)
filtred_assay = assay[assay["Hole_ID"].isin(intersection)]
filtred_assay

The next operation will delete every sample of the assay file that is not in the hyperspectral file and make sure that we have the exact same number of `Hole_ID` in both files.

In [ ]:
assay_final = hyperspec.merge(filtred_assay, on=["Hole_ID", "From", "To"], how="left")
assay_final.sort_values(by=["Hole_ID", "From"], inplace=True)
assay_final

### Merged Data Verification

This new file allows to make comparison between the data from the assay file (obtain by a XRF analysis) and the data from the hyperspectral analysis.

First we can compare the Fe weight percentage :

In [ ]:
sns.scatterplot(data=assay_final, x="Fe", y="Fe_pct");

Most of the measures are similar for both methods. We can do the same for the Al2O3 weight percentage :

In [ ]:
sns.scatterplot(data=assay_final, x="Al2O3_x", y="Al2O3_y");

In [ ]:
assay_final.drop(columns=["Al2O3_y", "LOI_x", "LOI_y"], inplace=True)
assay_final.rename(columns={"Al2O3_x": "Al2O3"}, inplace=True)

## GeoLime Drillholes Creation

The next command will use the Geo Lime dictionary to draw an interactive map of the ferric concentration for each method (one for the hyperspectral datas and one for the assay datas). Firs we need to import the survey and collar file to have all the informations about the drill cores.

In [ ]:
survey = geo.datasets.load("rocklea_dome/survey.csv")
collar = geo.datasets.load("rocklea_dome/collar.csv")

### Project Definition

In [ ]:
geo.Project().set_crs(CRS("EPSG:20350"))

### Drillholes Creation

#### Using Assay Data Only

In [ ]:
da = geo.create_drillholes(
    name="rck_assay", 
    collar=collar, 
    assays=assay, 
    survey=survey
)

In [ ]:
da.plot_2d(property="Fe", agg_method="mean", interactive_map=True)

#### Using Merged Data (Assay data & Hyperspectral data)

In [ ]:
df = geo.create_drillholes(
    name="rck_assay_final", 
    collar=collar, 
    assays=assay_final, 
    survey=survey
)

In [ ]:
df.to_file("../data/dh_hyper")

In [ ]:
df.plot_2d(property="Fe", agg_method="mean", interactive_map=True)

#### Using Hyperspectral Data only

We can do the same with hyperspectral data and draw the map of the average iron weight concentration given by these measures.

In [ ]:
dh = geo.create_drillholes(
    name="rck_hs", 
    collar=collar, 
    assays=hyperspec, 
    survey=survey
)

In [ ]:
dh.plot_2d(property="Fe_pct", agg_method="mean", interactive_map=True)

The first thing we can notice is that there is a concentration of high average iron concentration in the eastern drill core of the original assay data. That is on those drill core that the hyperspectral data have been taken. Then we can also notice the strong similarity between the iron average concentration between the hyperspectral data and the assay data for the same drill holes.

### 3D Visualisation

In [ ]:
df_pv = df.to_pyvista('Fe_pct')

In [ ]:
pl = pv.Plotter()
pl.add_mesh(df_pv.tube(radius=10))
pl.set_scale(zscale=20)

pl.show()